In [1]:
from itertools import product, combinations, cycle
from functools import reduce
from math import prod

In [38]:
fname = 'example.txt'
# fname = 'input.txt'
# fname = 'example2.txt'
        
with open(fname) as f:
    lines = f.readlines()

# [(on, [int(num) for num in rang.replace('x=', '').replace('y=', '').replace('z', '').replace('=', '').split('..') for rang in xyz.split(',')]) for on, xyz in [line.strip().split(' ') for line in lines]]

onoffs, ranges = [], []
# for line in lines[0:20]:
# for line in lines[:-2]:
for line in lines:
    onoff, xyz = line.strip().split(' ')
    ranges_letters = xyz.split(',')
    range_3d = tuple([tuple(int(val) for val in range_letter.split('=')[1].split('..')) for range_letter in ranges_letters])
    onoffs.append(onoff)
    ranges.append(range_3d)

instructions = list(zip(onoffs, ranges))
# instructions

In [67]:
instructions

[('on', ((-20, 26), (-36, 17), (-47, 7))),
 ('on', ((-20, 33), (-21, 23), (-26, 28))),
 ('on', ((-22, 28), (-29, 23), (-38, 16))),
 ('on', ((-46, 7), (-6, 46), (-50, -1))),
 ('on', ((-49, 1), (-3, 46), (-24, 28))),
 ('on', ((2, 47), (-22, 22), (-23, 27))),
 ('on', ((-27, 23), (-28, 26), (-21, 29))),
 ('on', ((-39, 5), (-6, 47), (-3, 44))),
 ('on', ((-30, 21), (-8, 43), (-13, 34))),
 ('on', ((-22, 26), (-27, 20), (-29, 19))),
 ('off', ((-48, -32), (26, 41), (-47, -37))),
 ('on', ((-12, 35), (6, 50), (-50, -2))),
 ('off', ((-48, -32), (-32, -16), (-15, -5))),
 ('on', ((-18, 26), (-33, 15), (-7, 46))),
 ('off', ((-40, -22), (-38, -28), (23, 41))),
 ('on', ((-16, 35), (-41, 10), (-47, 6))),
 ('off', ((-32, -23), (11, 30), (-14, 3))),
 ('on', ((-49, -5), (-3, 45), (-29, 18))),
 ('off', ((18, 30), (-20, -8), (-3, 13))),
 ('on', ((-41, 9), (-7, 43), (-33, 15)))]

In [32]:
def single_range_intersection(r1, r2):
    # https://scicomp.stackexchange.com/a/26260
    low, high = 0, 1 # assuming in order
    if len(r1) != 2 or len(r2) != 2:
        return []
    if r2[low] > r1[high] or r1[low] > r2[high]:
        return [] # no intersection
    else:
        return (max(r1[low], r2[low]), min(r1[high], r2[high]))
    

single_range_intersection((0, 2), (2, 4)) # NOTE THIS EDGE CASE

(2, 2)

In [33]:
def range_intersection(range_1, range_2):
    return [single_range_intersection(*ranges) for ranges in zip(range_1, range_2)]

r1 = [(-82717, -58814), (9792, 34867), (31729, 41188)]
r2 = [(-62226, -36572), (-17931, -2307), (64240, 74646)]

test_range_intersections = range_intersection(r1, r2)
test_range_intersections

[(-62226, -58814), [], []]

In [34]:
def range_intersection_idxs(idx_1, idx_2):
    return [single_range_intersection(*ranges) for ranges in zip(ranges[idx_1], ranges[idx_2])]

test_range_intersections = range_intersection_idxs(0, 1)
test_range_intersections

[(-20, 26), (-21, 17), (-26, 7)]

In [35]:
def intersection_size(intersection_3d):
    # TODO: is the '+1' correct
    return prod([max(rang)-min(rang)+1 if rang else 0 for rang in intersection_3d])


In [49]:
# find the set of all on idxs, and all off idxs
ons = set([ii for onoff, ii in zip(onoffs, range(len(ranges))) if onoff == 'on'])
offs = set(range(len(ranges))).difference(ons)
ons, offs

({0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 11, 13, 15, 17, 19}, {10, 12, 14, 16, 18})

In [46]:
debug_print = False
debug_print = True

running_total = 0

for onoff, ii in zip(onoffs, range(len(ranges))):
    
    if debug_print: print(f"testing set {ii} ({onoff})") 
    
    # test intersections with the sets before it only
    used_previous = set(range(ii))
    
    # add current set size, if on
    if onoff == 'on':
        running_total += intersection_size(ranges[ii])
    if debug_print: print(f"\t{running_total=}")
    
    for way in range(2, ii+2):
        if debug_print: print(f"\ttesting {way}-way intersections")
        eligible = set(range(ii)).intersection(used_previous)
        if debug_print: print(f"\teligible: {eligible}")
#         eligible = eligible.intersection(ons)
#         if debug_print: print(f"\teligible: {eligible} (after considering only 'on')")
        
        used_current = set()
        for comb in combinations(eligible, r=(way-1)):
            
            full_comb = tuple(list(comb) + [ii]) # including ii, the current one
            if debug_print: print(f"\t\t combination {full_comb}")
            
            way_int = reduce(range_intersection, [ranges[idx] for idx in full_comb])
            if not [] in way_int:
                # if a real intersection
                used_current.update(comb)
                size = intersection_size(way_int)
                    
                even = (way % 2 == 0)
                if even:
                    running_total -= size
                else:
                    running_total += size
                
                if debug_print: print(f"\t\t yes, {used_current=}, size: {size}, {running_total=}")
                    
            else:
                if debug_print: print("\t\t no")
        if debug_print: print(f"\tall intersecting with {ii}: {used_current}")
        if not used_current:
            # if no w-way intersections, definitely no w+1, ... way intersections
            if debug_print: print(f"\tNO {way}-WAY INTERSECTIONS, SKIPPING REMAINING...")
#             print(f"\tNO {way}-WAY INTERSECTIONS, SKIPPING REMAINING...")    
            break
        used_previous = used_current
#     if ii > 3: break


# correct_ans = 2758514936282235
correct_ans = 590784
print(running_total, correct_ans, correct_ans-running_total)

testing set 0 (on)
	running_total=139590
testing set 1 (on)
	running_total=273240
	testing 2-way intersections
	eligible: {0}
		 combination (0, 1)
		 yes, used_current={0}, size: 62322, running_total=210918
	all intersecting with 1: {0}
testing set 2 (on)
	running_total=359583
	testing 2-way intersections
	eligible: {0, 1}
		 combination (0, 2)
		 yes, used_current={0}, size: 101614, running_total=257969
		 combination (1, 2)
		 yes, used_current={0, 1}, size: 94815, running_total=163154
	all intersecting with 2: {0, 1}
	testing 3-way intersections
	eligible: {0, 1}
		 combination (0, 1, 2)
		 yes, used_current={0, 1}, size: 62322, running_total=225476
	all intersecting with 2: {0, 1}
testing set 3 (on)
	running_total=368576
	testing 2-way intersections
	eligible: {0, 1, 2}
		 combination (0, 3)
		 yes, used_current={0}, size: 31584, running_total=336992
		 combination (1, 3)
		 yes, used_current={0, 1}, size: 21840, running_total=315152
		 combination (2, 3)
		 yes, used_current={0, 

		 yes, used_current={0, 1, 2, 3, 4, 5, 6, 7, 8}, size: 6006, running_total=453296
		 combination (0, 1, 3, 4, 7, 8, 9)
		 yes, used_current={0, 1, 2, 3, 4, 5, 6, 7, 8}, size: 1386, running_total=454682
		 combination (0, 1, 3, 5, 6, 7, 9)
		 yes, used_current={0, 1, 2, 3, 4, 5, 6, 7, 8}, size: 288, running_total=454970
		 combination (0, 1, 3, 5, 6, 8, 9)
		 yes, used_current={0, 1, 2, 3, 4, 5, 6, 7, 8}, size: 1872, running_total=456842
		 combination (0, 1, 3, 5, 7, 8, 9)
		 yes, used_current={0, 1, 2, 3, 4, 5, 6, 7, 8}, size: 288, running_total=457130
		 combination (0, 1, 3, 6, 7, 8, 9)
		 yes, used_current={0, 1, 2, 3, 4, 5, 6, 7, 8}, size: 1872, running_total=459002
		 combination (0, 1, 4, 5, 6, 7, 9)
		 no
		 combination (0, 1, 4, 5, 6, 8, 9)
		 no
		 combination (0, 1, 4, 5, 7, 8, 9)
		 no
		 combination (0, 1, 4, 6, 7, 8, 9)
		 yes, used_current={0, 1, 2, 3, 4, 5, 6, 7, 8}, size: 5082, running_total=464084
		 combination (0, 1, 5, 6, 7, 8, 9)
		 yes, used_current={0, 1, 2, 3,

		 combination (2, 4, 5, 6, 8, 9, 11)
		 no
		 combination (2, 4, 5, 7, 8, 9, 11)
		 no
		 combination (2, 4, 6, 7, 8, 9, 11)
		 yes, used_current={0, 1, 2, 3, 4, 5, 6, 7, 8, 9}, size: 420, running_total=568912
		 combination (2, 5, 6, 7, 8, 9, 11)
		 yes, used_current={0, 1, 2, 3, 4, 5, 6, 7, 8, 9}, size: 120, running_total=569032
		 combination (3, 4, 5, 6, 7, 8, 11)
		 no
		 combination (3, 4, 5, 6, 7, 9, 11)
		 no
		 combination (3, 4, 5, 6, 8, 9, 11)
		 no
		 combination (3, 4, 5, 7, 8, 9, 11)
		 no
		 combination (3, 4, 6, 7, 8, 9, 11)
		 yes, used_current={0, 1, 2, 3, 4, 5, 6, 7, 8, 9}, size: 420, running_total=569452
		 combination (3, 5, 6, 7, 8, 9, 11)
		 yes, used_current={0, 1, 2, 3, 4, 5, 6, 7, 8, 9}, size: 120, running_total=569572
		 combination (4, 5, 6, 7, 8, 9, 11)
		 no
	all intersecting with 11: {0, 1, 2, 3, 4, 5, 6, 7, 8, 9}
	testing 8-way intersections
	eligible: {0, 1, 2, 3, 4, 5, 6, 7, 8, 9}
		 combination (0, 1, 2, 3, 4, 5, 6, 11)
		 no
		 combination (0, 1, 2,

		 combination (0, 2, 5, 8, 9, 13)
		 yes, used_current={0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 11}, size: 7200, running_total=785374
		 combination (0, 2, 5, 8, 11, 13)
		 yes, used_current={0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 11}, size: 1200, running_total=784174
		 combination (0, 2, 5, 9, 11, 13)
		 yes, used_current={0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 11}, size: 1500, running_total=782674
		 combination (0, 2, 6, 7, 8, 13)
		 yes, used_current={0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 11}, size: 5808, running_total=776866
		 combination (0, 2, 6, 7, 9, 13)
		 yes, used_current={0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 11}, size: 5808, running_total=771058
		 combination (0, 2, 6, 7, 11, 13)
		 yes, used_current={0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 11}, size: 360, running_total=770698
		 combination (0, 2, 6, 8, 9, 13)
		 yes, used_current={0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 11}, size: 14400, running_total=756298
		 combination (0, 2, 6, 8, 11, 13)
		 yes, used_current={0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 11}, size: 2040, running_total=754

		 combination (0, 2, 3, 4, 5, 9, 11, 13)
		 no
		 combination (0, 2, 3, 4, 6, 7, 8, 13)
		 yes, used_current={0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 11}, size: 1140, running_total=599636
		 combination (0, 2, 3, 4, 6, 7, 9, 13)
		 yes, used_current={0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 11}, size: 1140, running_total=598496
		 combination (0, 2, 3, 4, 6, 7, 11, 13)
		 yes, used_current={0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 11}, size: 280, running_total=598216
		 combination (0, 2, 3, 4, 6, 8, 9, 13)
		 yes, used_current={0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 11}, size: 2660, running_total=595556
		 combination (0, 2, 3, 4, 6, 8, 11, 13)
		 yes, used_current={0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 11}, size: 840, running_total=594716
		 combination (0, 2, 3, 4, 6, 9, 11, 13)
		 yes, used_current={0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 11}, size: 840, running_total=593876
		 combination (0, 2, 3, 4, 7, 8, 9, 13)
		 yes, used_current={0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 11}, size: 1140, running_total=592736
		 combination (0, 2, 3, 4, 7, 8, 1

...

		 no
		 combination (2, 5, 6, 8, 9, 11, 13, 17, 19)
		 no
		 combination (2, 5, 6, 8, 9, 11, 15, 16, 19)
		 no
		 combination (2, 5, 6, 8, 9, 11, 15, 17, 19)
		 no
		 combination (2, 5, 6, 8, 9, 11, 16, 17, 19)
		 no
		 combination (2, 5, 6, 8, 9, 13, 15, 16, 19)
		 no
		 combination (2, 5, 6, 8, 9, 13, 15, 17, 19)
		 no
		 combination (2, 5, 6, 8, 9, 13, 16, 17, 19)
		 no
		 combination (2, 5, 6, 8, 9, 15, 16, 17, 19)
		 no
		 combination (2, 5, 6, 8, 11, 13, 15, 16, 19)
		 no
		 combination (2, 5, 6, 8, 11, 13, 15, 17, 19)
		 no
		 combination (2, 5, 6, 8, 11, 13, 16, 17, 19)
		 no
		 combination (2, 5, 6, 8, 11, 15, 16, 17, 19)
		 no
		 combination (2, 5, 6, 8, 13, 15, 16, 17, 19)
		 no
		 combination (2, 5, 6, 9, 11, 13, 15, 16, 19)
		 no
		 combination (2, 5, 6, 9, 11, 13, 15, 17, 19)
		 no
		 combination (2, 5, 6, 9, 11, 13, 16, 17, 19)
		 no
		 combination (2, 5, 6, 9, 11, 15, 16, 17, 19)
		 no
		 combination (2, 5, 6, 9, 13, 15, 16, 17, 19)
		 no
		 combination (2, 5, 6, 11, 1

		 no
		 combination (0, 1, 2, 4, 5, 7, 9, 11, 17, 19)
		 no
		 combination (0, 1, 2, 4, 5, 7, 9, 13, 15, 19)
		 no
		 combination (0, 1, 2, 4, 5, 7, 9, 13, 17, 19)
		 no
		 combination (0, 1, 2, 4, 5, 7, 9, 15, 17, 19)
		 no
		 combination (0, 1, 2, 4, 5, 7, 11, 13, 15, 19)
		 no
		 combination (0, 1, 2, 4, 5, 7, 11, 13, 17, 19)
		 no
		 combination (0, 1, 2, 4, 5, 7, 11, 15, 17, 19)
		 no
		 combination (0, 1, 2, 4, 5, 7, 13, 15, 17, 19)
		 no
		 combination (0, 1, 2, 4, 5, 8, 9, 11, 13, 19)
		 no
		 combination (0, 1, 2, 4, 5, 8, 9, 11, 15, 19)
		 no
		 combination (0, 1, 2, 4, 5, 8, 9, 11, 17, 19)
		 no
		 combination (0, 1, 2, 4, 5, 8, 9, 13, 15, 19)
		 no
		 combination (0, 1, 2, 4, 5, 8, 9, 13, 17, 19)
		 no
		 combination (0, 1, 2, 4, 5, 8, 9, 15, 17, 19)
		 no
		 combination (0, 1, 2, 4, 5, 8, 11, 13, 15, 19)
		 no
		 combination (0, 1, 2, 4, 5, 8, 11, 13, 17, 19)
		 no
		 combination (0, 1, 2, 4, 5, 8, 11, 15, 17, 19)
		 no
		 combination (0, 1, 2, 4, 5, 8, 13, 15, 17, 19)
		

		 yes, used_current={0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 11, 13, 15, 17}, size: 160, running_total=595860
		 combination (0, 3, 4, 7, 8, 9, 11, 15, 17, 19)
		 yes, used_current={0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 11, 13, 15, 17}, size: 80, running_total=595780
		 combination (0, 3, 4, 7, 8, 9, 13, 15, 17, 19)
		 yes, used_current={0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 11, 13, 15, 17}, size: 504, running_total=595276
		 combination (0, 3, 4, 7, 8, 11, 13, 15, 17, 19)
		 yes, used_current={0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 11, 13, 15, 17}, size: 80, running_total=595196
		 combination (0, 3, 4, 7, 9, 11, 13, 15, 17, 19)
		 yes, used_current={0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 11, 13, 15, 17}, size: 80, running_total=595116
		 combination (0, 3, 4, 8, 9, 11, 13, 15, 17, 19)
		 yes, used_current={0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 11, 13, 15, 17}, size: 240, running_total=594876
		 combination (0, 3, 5, 6, 7, 8, 9, 11, 13, 19)
		 yes, used_current={0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 11, 13, 15, 17}, size: 80, running_total=59

		 combination (0, 1, 2, 3, 4, 6, 7, 11, 15, 17, 19)
		 yes, used_current={0, 1, 2, 3, 4, 6, 7, 8, 9, 11, 13, 15, 17}, size: 80, running_total=500544
		 combination (0, 1, 2, 3, 4, 6, 7, 13, 15, 17, 19)
		 yes, used_current={0, 1, 2, 3, 4, 6, 7, 8, 9, 11, 13, 15, 17}, size: 504, running_total=501048
		 combination (0, 1, 2, 3, 4, 6, 8, 9, 11, 13, 19)
		 yes, used_current={0, 1, 2, 3, 4, 6, 7, 8, 9, 11, 13, 15, 17}, size: 840, running_total=501888
		 combination (0, 1, 2, 3, 4, 6, 8, 9, 11, 15, 19)
		 yes, used_current={0, 1, 2, 3, 4, 6, 7, 8, 9, 11, 13, 15, 17}, size: 840, running_total=502728
		 combination (0, 1, 2, 3, 4, 6, 8, 9, 11, 17, 19)
		 yes, used_current={0, 1, 2, 3, 4, 6, 7, 8, 9, 11, 13, 15, 17}, size: 1152, running_total=503880
		 combination (0, 1, 2, 3, 4, 6, 8, 9, 13, 15, 19)
		 yes, used_current={0, 1, 2, 3, 4, 6, 7, 8, 9, 11, 13, 15, 17}, size: 1764, running_total=505644
		 combination (0, 1, 2, 3, 4, 6, 8, 9, 13, 17, 19)
		 yes, used_current={0, 1, 2, 3, 4, 6, 7, 8,

		 combination (0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 13, 19)
		 no
		 combination (0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 15, 19)
		 no
		 combination (0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 17, 19)
		 no
		 combination (0, 1, 2, 3, 4, 5, 6, 7, 8, 11, 13, 19)
		 no
		 combination (0, 1, 2, 3, 4, 5, 6, 7, 8, 11, 15, 19)
		 no
		 combination (0, 1, 2, 3, 4, 5, 6, 7, 8, 11, 17, 19)
		 no
		 combination (0, 1, 2, 3, 4, 5, 6, 7, 8, 13, 15, 19)
		 no
		 combination (0, 1, 2, 3, 4, 5, 6, 7, 8, 13, 17, 19)
		 no
		 combination (0, 1, 2, 3, 4, 5, 6, 7, 8, 15, 17, 19)
		 no
		 combination (0, 1, 2, 3, 4, 5, 6, 7, 9, 11, 13, 19)
		 no
		 combination (0, 1, 2, 3, 4, 5, 6, 7, 9, 11, 15, 19)
		 no
		 combination (0, 1, 2, 3, 4, 5, 6, 7, 9, 11, 17, 19)
		 no
		 combination (0, 1, 2, 3, 4, 5, 6, 7, 9, 13, 15, 19)
		 no
		 combination (0, 1, 2, 3, 4, 5, 6, 7, 9, 13, 17, 19)
		 no
		 combination (0, 1, 2, 3, 4, 5, 6, 7, 9, 15, 17, 19)
		 no
		 combination (0, 1, 2, 3, 4, 5, 6, 7, 11, 13, 15, 19)
		 no
		 combination (0, 1, 2, 3

# try evaluating intersections with `off` as null, empty

In [104]:
def find_total_intersection_size(onoffs, ranges, debug_print=False):

    ons = set([ii for onoff, ii in zip(onoffs, range(len(ranges))) if onoff == 'on'])
    offs = set(range(len(ranges))).difference(ons)
    
    running_total = 0

    for onoff, ii in zip(onoffs, range(len(ranges))):

        if debug_print: print(f"testing set {ii} ({onoff})") 

        # test intersections with the sets before it only
        used_previous = set(range(ii))

        # add current set size, if on
        if onoff == 'on':
            running_total += intersection_size(ranges[ii])
        if debug_print: print(f"\t{running_total=}")

        for way in range(2, ii+2):
            if debug_print: print(f"\ttesting {way}-way intersections")

            eligible = set(range(ii)).intersection(used_previous)
            if debug_print: print(f"\teligible: {eligible}")

            even = (way % 2 == 0)

            if even:
                eligible = eligible.intersection(ons)
                if debug_print: print(f"\teligible: {eligible} (after considering only 'on')")

            used_current = set()
            for comb in combinations(eligible, r=(way-1)):

                full_comb = tuple([ii] + list(comb)) # including ii, the current one
                if debug_print: print(f"\t\t combination {full_comb}")

    #             way_int = reduce(range_intersection_idxs, full_comb) # list indices must be integers or slices, not list
                way_int = reduce(range_intersection, [ranges[idx] for idx in full_comb])

                if not [] in way_int:
                    # if a real intersection
                    used_current.update(comb)
                    size = intersection_size(way_int)

                    rel_offs = set(full_comb).intersection(offs)
    #                 if size == 3600:
#                     if rel_offs:
#                         print(f"{full_comb=}\t{rel_offs}\t{size=}")

                    if even:
                        running_total -= size
                    else:
                        running_total += size

                    if debug_print: print(f"\t\t yes, {used_current=}, size: {size}, {running_total=}")

                else:
                    if debug_print: print("\t\t no")
            if debug_print: print(f"\tall intersecting with {ii}: {used_current}")
            if not used_current:
                # if no w-way intersections, definitely no w+1, ... way intersections
                if debug_print: print(f"\tNO {way}-WAY INTERSECTIONS, SKIPPING REMAINING...")
    #             print(f"\tNO {way}-WAY INTERSECTIONS, SKIPPING REMAINING...")    
                break
            used_previous = used_current
    #     if ii > 10: break
    
    return running_total

# correct_ans = 2758514936282235
correct_ans = 590784
ans = find_total_intersection_size(onoffs, ranges)
print(ans, correct_ans, correct_ans-running_total)

587184 590784 3600


# test cases

In [76]:
t1 = [('on', ((-20, 26), (-36, 17), (-47, 7))),
 ('on', ((-20, 33), (-21, 23), (-26, 28))),
 ('on', ((-22, 28), (-29, 23), (-38, 16))),]

onoffs1, ranges1 = zip(*t1)

find_total_intersection_size(onoffs1, ranges1)

225476

In [92]:

onoffs2 = ["on"]
ranges2 = [((0, 9), (0, 9), (0, 0)),
           ((0, 9), (0, 9), (0, 0)),
          ]

assert find_total_intersection_size(onoffs2, ranges2) == 100

In [95]:
onoffs3 = ["off", "off"]
ranges3 = [((0, 9), (0, 9), (0, 0)),
           ((0, 99), (0, 99), (0, 0)),
          ]
assert find_total_intersection_size(onoffs3, ranges3, debug_print=True) == 0, find_total_intersection_size(onoffs3, ranges3)

testing set 0 (off)
	running_total=0
testing set 1 (off)
	running_total=0
	testing 2-way intersections
	eligible: {0}
	eligible: set() (after considering only 'on')
	all intersecting with 1: set()
	NO 2-WAY INTERSECTIONS, SKIPPING REMAINING...


In [97]:
onoffs3 = ["off", "off", "off"]
ranges3 = [((0, 9), (0, 9), (0, 0)),
           ((0, 99), (0, 99), (0, 0)),
           ((0, 999), (0, 999), (0, 0)),
          ]
assert find_total_intersection_size(onoffs3, ranges3, debug_print=True) == 0, find_total_intersection_size(onoffs3, ranges3)

testing set 0 (off)
	running_total=0
testing set 1 (off)
	running_total=0
	testing 2-way intersections
	eligible: {0}
	eligible: set() (after considering only 'on')
	all intersecting with 1: set()
	NO 2-WAY INTERSECTIONS, SKIPPING REMAINING...
testing set 2 (off)
	running_total=0
	testing 2-way intersections
	eligible: {0, 1}
	eligible: set() (after considering only 'on')
	all intersecting with 2: set()
	NO 2-WAY INTERSECTIONS, SKIPPING REMAINING...


In [98]:

onoffs3 = ["on", "off"]
ranges3 = [((0, 9), (0, 9), (0, 0)),
           ((0, 99), (0, 99), (0, 0)),
          ]
assert find_total_intersection_size(onoffs3, ranges3, debug_print=True) == 0, find_total_intersection_size(onoffs3, ranges3)


testing set 0 (on)
	running_total=100
testing set 1 (off)
	running_total=100
	testing 2-way intersections
	eligible: {0}
	eligible: {0} (after considering only 'on')
		 combination (1, 0)
		 yes, used_current={0}, size: 100, running_total=0
	all intersecting with 1: {0}


In [99]:

onoffs3 = ["off", "on"]
ranges3 = [((0, 9), (0, 9), (0, 0)),
           ((0, 99), (0, 99), (0, 0)),
          ]

assert find_total_intersection_size(onoffs3, ranges3, debug_print=True) == 10000, find_total_intersection_size(onoffs3, ranges3)



testing set 0 (off)
	running_total=0
testing set 1 (on)
	running_total=10000
	testing 2-way intersections
	eligible: {0}
	eligible: set() (after considering only 'on')
	all intersecting with 1: set()
	NO 2-WAY INTERSECTIONS, SKIPPING REMAINING...


In [105]:
# test that all-off regions don't subtract from later overlapping 'on' regions 

onoffs3 = ["on", "off", "on"]
ranges3 = [((0, 1), (0, 1), (0, 0)),
           ((0, 2), (0, 2), (0, 0)),
           ((0, 9), (0, 9), (0, 0)),
          ]
assert find_total_intersection_size(onoffs3, ranges3, debug_print=True) == 0, find_total_intersection_size(onoffs3, ranges3)


testing set 0 (on)
	running_total=4
testing set 1 (off)
	running_total=4
	testing 2-way intersections
	eligible: {0}
	eligible: {0} (after considering only 'on')
		 combination (1, 0)
		 yes, used_current={0}, size: 4, running_total=0
	all intersecting with 1: {0}
testing set 2 (on)
	running_total=100
	testing 2-way intersections
	eligible: {0, 1}
	eligible: {0} (after considering only 'on')
		 combination (2, 0)
		 yes, used_current={0}, size: 4, running_total=96
	all intersecting with 2: {0}
	testing 3-way intersections
	eligible: {0}
	all intersecting with 2: set()
	NO 3-WAY INTERSECTIONS, SKIPPING REMAINING...


AssertionError: 96